In [4]:
import io
import os
import cv2
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.image as mpimg
from tqdm import tqdm

In [5]:
path = 'dados/CAPTCHA-10k'
save_path = 'dados/processed'
labels_folder = 'labels10k'
if not os.path.exists(save_path):
    os.makedirs(save_path)
num_chars = 6

In [6]:
labels_dict = {}
labels_path = 'dados/CAPTCHA-10k/labels10k'

for fname in os.listdir(labels_path):
    if not fname.endswith('.txt'):
        continue

    base_name = os.path.splitext(fname)[0]
    full_path = os.path.join(labels_path, fname)

    with open(full_path, 'r') as f:
        content = f.read().strip()
        labels_dict[base_name] = content


In [7]:
def save_cleaned_image(path, folder, filename, save_path):
    img_path = os.path.join(path, folder, filename)
    img_gray = cv2.imread(img_path, cv2.IMREAD_GRAYSCALE)

    if img_gray is None:
        print(f"Erro: Não foi possível carregar a imagem em {img_path}")
        return

    # Remoção de ruído
    denoised_img = cv2.medianBlur(img_gray, 3)

    # Binarização (fundo preto, texto branco)
    threshold_value = 80
    _, binary_cleaned_img = cv2.threshold(denoised_img, threshold_value, 255, cv2.THRESH_BINARY_INV)

    # Erosão leve para tentar separar caracteres colados
    kernel = np.ones((2, 2), np.uint8)
    binary_cleaned_img = cv2.erode(binary_cleaned_img, kernel, iterations=1)

    binary_cleaned_img = cv2.dilate(binary_cleaned_img, kernel, iterations=1)

    # Criar pasta de saída
    output_folder_path = os.path.join(save_path, folder, 'cleanImage')
    os.makedirs(output_folder_path, exist_ok=True)

    # Salvar imagem final
    cleaned_filename = f"{os.path.splitext(filename)[0]}{os.path.splitext(filename)[1]}"
    full_output_path = os.path.join(output_folder_path, cleaned_filename)
    cv2.imwrite(full_output_path, binary_cleaned_img)

In [8]:
for folder in tqdm(os.listdir(path), desc="Processing folders"):
    if os.path.isdir(os.path.join(path, folder)) and folder != labels_folder:
        for filename in tqdm(os.listdir(os.path.join(path, folder)), desc=f"Cleaning {folder}", leave=False):
            if filename.endswith('.jpg'):
                save_cleaned_image(path, folder, filename, save_path)


Processing folders: 100%|██████████| 4/4 [01:10<00:00, 17.52s/it]


In [ ]:
def split_image(path, folder, filename, save_path,
                        margin=12, max_char_width=48, min_advance=8, debug=False):
    img_path = os.path.join(path, folder, filename)
    img = cv2.imread(img_path, cv2.IMREAD_GRAYSCALE)

    if img is None:
        print(f"Erro: Não foi possível carregar a imagem em {img_path}")
        return

    height, width = img.shape
    step = width / 6
    cut_points = [int(round(i * step)) for i in range(7)]  

    os.makedirs(save_path, exist_ok=True)
    base_name, ext = os.path.splitext(filename)

    if base_name not in labels_dict or len(labels_dict[base_name]) != 6:
        print(f"Label ausente ou incompleto para: {base_name}")
        return

    label_seq = labels_dict[base_name]

    prev_end_x = 0  # Para controlar avanço mínimo entre cortes

    for i in range(6):
        # Garante que o próximo corte avance pelo menos 'min_advance' pixels
        base_start_x = max(prev_end_x + min_advance, cut_points[i])
        base_end_x = cut_points[i + 1]

        region = img[:, base_start_x:base_end_x]
        proj = np.sum(region, axis=0)

        region_width = base_end_x - base_start_x
        center_local = int(np.argmax(proj))

        # Limitar deslocamento do centro (máx 25% da largura da região)
        center_shift = center_local - region_width // 2
        max_shift = region_width // 4
        clamped_shift = int(np.clip(center_shift, -max_shift, max_shift))
        adjusted_center = base_start_x + region_width // 2 + clamped_shift

        # Define faixa de corte com margem
        start_x = int(max(0, adjusted_center - region_width // 2 - margin))
        end_x = int(min(width, adjusted_center + region_width // 2 + margin))

        # Impor limite máximo de largura
        if end_x - start_x > max_char_width:
            extra = (end_x - start_x - max_char_width) // 2
            start_x += extra
            end_x -= extra

        # Atualiza o fim da faixa atual para o controle do próximo corte
        prev_end_x = end_x

        char_img = img[:, start_x:end_x]
        char_label = label_seq[i]

        # Salvar
        save_path_full = os.path.join(save_path, char_label)
        os.makedirs(save_path_full, exist_ok=True)

        char_filename = f"{base_name}_{i}{ext}"
        char_filename = f"{base_name}_{i}{ext}"
        final_path = os.path.join(save_path_full, char_filename)
        cv2.imwrite(final_path, char_img)

        # Debug visual
        if debug:
            img_debug = cv2.cvtColor(img, cv2.COLOR_GRAY2BGR)
            cv2.rectangle(img_debug, (start_x, 0), (end_x, height), (0, 255, 0), 2)
            cv2.imshow(f"Char {i}", img_debug)
            cv2.waitKey(0)

    if debug:
        cv2.destroyAllWindows()

In [10]:
conjuntos = ['treinamento', 'teste', 'validacao']
clean_base_path = '/home/bernardo/TP2-ICV/dados/processed'
for conjunto in conjuntos:
    folder_clean = os.path.join(conjunto, 'cleanImage')
    full_clean_folder = os.path.join(clean_base_path, folder_clean)

    for filename in tqdm(os.listdir(full_clean_folder), desc=f"Segmentando {conjunto}"):
        if filename.endswith('.jpg'):
            save_folder = os.path.join(clean_base_path, conjunto)

            split_image(
                path=clean_base_path,
                folder=folder_clean,        
                filename=filename,
                save_path=save_folder,      
                debug=False
            )


Segmentando treinamento:   1%|          | 89/8000 [00:00<00:17, 447.87it/s]

Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005583_0.jpg/O
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005583_1.jpg/7
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005583_2.jpg/0
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005583_3.jpg/R
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005583_4.jpg/R
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005583_5.jpg/Y
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002926_0.jpg/2
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002926_1.jpg/4
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002926_2.jpg/7
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002926_3.jpg/C
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002926_4.jpg/W
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002926_5.jpg/E
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/004463_0.jpg/8
Salvo: /home/bernardo/TP2-ICV/dados/processed/trein

Segmentando treinamento:   2%|▏         | 198/8000 [00:00<00:15, 511.17it/s]

Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005177_0.jpg/P
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005177_1.jpg/C
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005177_2.jpg/Y
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005177_3.jpg/3
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005177_4.jpg/N
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005177_5.jpg/D
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005714_0.jpg/N
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005714_1.jpg/J
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005714_2.jpg/4
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005714_3.jpg/G
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005714_4.jpg/D
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/005714_5.jpg/4
Salvo: /home/bernardo/TP2-ICV/dados/processed/treinamento/002857_0.jpg/7
Salvo: /home/bernardo/TP2-ICV/dados/processed/trein

Segmentando treinamento:   3%|▎         | 250/8000 [00:00<00:15, 505.88it/s]

...

Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008220_2.jpg/R
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008220_3.jpg/9
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008220_4.jpg/F
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008220_5.jpg/W
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008717_0.jpg/5
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008717_1.jpg/7
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008717_2.jpg/3
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008717_3.jpg/Z
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008717_4.jpg/K
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008717_5.jpg/B
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008266_0.jpg/2
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008266_1.jpg/8
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008266_2.jpg/5
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008266_3.jpg/9
Salvo:

Segmentando validacao:  91%|█████████ | 906/1000 [00:03<00:00, 285.36it/s]

Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008058_5.jpg/9
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008533_0.jpg/L
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008533_1.jpg/X
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008533_2.jpg/8
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008533_3.jpg/M
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008533_4.jpg/4
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008533_5.jpg/D
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008302_0.jpg/Z
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008302_1.jpg/V
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008302_2.jpg/4
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008302_3.jpg/W
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008302_4.jpg/P
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008302_5.jpg/7
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008787_0.jpg/4
Salvo:

Segmentando validacao: 100%|██████████| 1000/1000 [00:03<00:00, 260.96it/s]

Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008555_0.jpg/7
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008555_1.jpg/L
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008555_2.jpg/9
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008555_3.jpg/1
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008555_4.jpg/8
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008555_5.jpg/3
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008646_0.jpg/U
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008646_1.jpg/6
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008646_2.jpg/Z
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008646_3.jpg/P
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008646_4.jpg/T
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008646_5.jpg/S
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008195_0.jpg/8
Salvo: /home/bernardo/TP2-ICV/dados/processed/validacao/008195_1.jpg/K
Salvo: